# Vegetation Phenology

* **Products used:** 
[s2_l2a](https://explorer.digitalearth.africa/s2_l2a),
[crop_mask](https://explorer.digitalearth.africa/products/crop_mask)

## Background
Phenology is the study of plant and animal life cycles in the context of the seasons.
It can be useful in understanding the life cycle trends of crops and how the growing seasons are affected by changes in climate.
For more information, see the [USGS page on deriving phenology from NDVI time-series](https://www.usgs.gov/land-resources/eros/phenology/science/deriving-phenological-metrics-ndvi?qt-science_center_objects=0#qt-science_center_objects).

## Matt's suggestions

- Start a fresh notebook
- Use the shapefile and geopandas parts above to makea geopandas Dataframe of points, and cooresponding polygon
- Start a dask LocalCluster
- Datacube load for the bounds of the polygon = `data`
- for each point in the geopandas dataframe,
   - get the timeseries for the point from `data`, e.g. using `data.sel(latitude=lat, longitude=lon)`. See https://docs.xarray.dev/en/stable/user-guide/indexing.html
   - plot or do something with each timeseries

## Getting started

To run this analysis, run all the cells in the notebook, starting with the "Load packages" cell. 

### Load packages
Load key Python packages and supporting functions for the analysis.

In [1]:
%matplotlib inline

import datetime as dt
from datetime import datetime
import os, sys

import datacube
import geopandas as gpd
import matplotlib as mpl
import matplotlib.pyplot as plt
import mpl_toolkits.axisartist as AA
import numpy as np
import pandas as pd
import xarray as xr
from datacube.utils.rio import configure_s3_access
from datacube.utils.geometry import Geometry
from datacube.utils import masking  # https://github.com/opendatacube/datacube-core/blob/develop/datacube/utils/masking.py
from odc.algo import enum_to_bool   # https://github.com/opendatacube/odc-tools/blob/develop/libs/algo/odc/algo/_masking.py
from mpl_toolkits.axes_grid1 import host_subplot

repo1 = '/home/jovyan/easi-notebooks'
if repo1 not in sys.path: sys.path.append(repo1)

os.environ['USE_PYGEOS'] = '0'
from easi_tools import EasiDefaults, notebook_utils
easi = EasiDefaults()

repo = '/home/jovyan/deafrica-sandbox-notebooks/Tools'
if repo not in sys.path: sys.path.append(repo)

from deafrica_tools.areaofinterest import define_area
from deafrica_tools.bandindices import calculate_indices
from deafrica_tools.datahandling import load_ard
from deafrica_tools.plotting import display_map, rgb
from deafrica_tools.spatial import xr_rasterize
from deafrica_tools.temporal import temporal_statistics, xr_phenology

Successfully found configuration for deployment "asia"


### Dask cluster

For local cluster options, see https://docs.dask.org/en/latest/setup/single-distributed.html

The Dask Dashboard link shown after the following cell is a helpful resource to explore the activity and state of your dask cluster.

In [2]:
# cluster, client = notebook_utils.initialize_dask(use_gateway=False)
# display(cluster if cluster else client)
# print(notebook_utils.localcluster_dashboard(client, server=easi.hub))

# Use EASI 'dask gateway' cluster
cluster, client = notebook_utils.initialize_dask(use_gateway=True, workers=(1,5))
display(client)

An existing cluster was found. Connecting to: easihub.27cf76d989534b8286f88dbcd24b8bd7


<Client: 'tls://10.0.44.204:8786' processes=1 threads=8, memory=28.00 GiB>

### Connect to the datacube

Connect to the datacube so we can access DE Africa data.
The `app` parameter is a unique name for the analysis which is based on the notebook file name.

In [3]:
dc = datacube.Datacube(app="Vegetation_phenology")
configure_s3_access(aws_unsigned=False, requester_pays=True, client=client)

### Analysis parameters

The following cell sets important parameters for the analysis:

* `veg_proxy`: Band index to use as a proxy for vegetation health e.g. `'NDVI'` or `'EVI'`.
* `lat`: The central latitude to analyse (e.g. `-10.6996`).
* `lon`: The central longitude to analyse (e.g. `35.2708`).
* `buffer`: The number of square degrees to load around the central latitude and longitude.
For reasonable loading times, set this as `0.1` or lower.
* `time_range`: The year range to analyse (e.g. `('2019-01', '2019-06')`).

#### Select location
To define the area of interest, there are two methods available:

1. By specifying the latitude, longitude, and buffer. This method requires you to input the central latitude, central longitude, and the buffer value in square degrees around the center point you want to analyze. For example, `lat = 10.338`, `lon = -1.055`, and `buffer = 0.1` will select an area with a radius of 0.1 square degrees around the point with coordinates (10.338, -1.055).

2. By uploading a polygon as a `GeoJSON or Esri Shapefile`. If you choose this option, you will need to upload the geojson or ESRI shapefile into the Sandbox using Upload Files button <img align="top" src="../Supplementary_data/upload_files_icon.png"> in the top left corner of the Jupyter Notebook interface. ESRI shapefiles must be uploaded with all the related files `(.cpg, .dbf, .shp, .shx)`. Once uploaded, you can use the shapefile or geojson to define the area of interest. Remember to update the code to call the file you have uploaded.

To use one of these methods, you can uncomment the relevant line of code and comment out the other one. To comment out a line, add the `"#"` symbol before the code you want to comment out. By default, the first option which defines the location using latitude, longitude, and buffer is being used.

In [4]:
# Set the vegetation proxy to use
veg_proxy = "NDVI"

time_range = ("2022-10-01", "2023-04-30")

In [5]:
# Method 2: Use a polygon as a GeoJSON or Esri Shapefile.
# aoi = define_area(vector_path='/home/jovyan/input_data/lentil_22-23.shp')
gdf = gpd.read_file('/home/jovyan/input_data/lentil_22-23.shp')
geopolygon_gdf = gpd.GeoDataFrame(geometry=[gdf.unary_union.convex_hull], crs=gdf.crs)

# Get the latitude and longitude range of the geopolygon
buffer = 0.001  # approximate 100 m
lat_range = (geopolygon_gdf.total_bounds[1]-buffer, geopolygon_gdf.total_bounds[3]+buffer)
lon_range = (geopolygon_gdf.total_bounds[0]-buffer, geopolygon_gdf.total_bounds[2]+buffer)

In [6]:
lat_range

(24.3862745, 24.4360797)

In [7]:
display(geopolygon_gdf)
display(gdf)

geometry
0  POLYGON ((88.46732 24.38727, 88.44501 24.39276...

start   latitude  longitude  Yield(t/ha                   geometry
0    2023-02-28  24.425337  88.413161    0.898200  POINT (88.41316 24.42534)
1    2023-02-28  24.425380  88.412949    0.898200  POINT (88.41295 24.42538)
2    2023-03-05  24.408209  88.463824    0.898200  POINT (88.46382 24.40821)
3    2023-03-05  24.408758  88.463470    0.748500  POINT (88.46347 24.40876)
4    2023-03-05  24.408059  88.462607    1.047900  POINT (88.46261 24.40806)
..          ...        ...        ...         ...                        ...
198  2023-04-27  24.410867  88.424580    1.085325  POINT (88.42458 24.41087)
199  2023-04-27  24.410865  88.424590    0.935625  POINT (88.42459 24.41087)
200  2023-04-27  24.410040  88.424343    0.973050  POINT (88.42434 24.41004)
201  2023-04-27  24.409848  88.424048    0.860775  POINT (88.42405 24.40985)
202  2023-04-27  24.409549  88.424274    0.935625  POINT (88.42427 24.40955)

[203 rows x 5 columns]

## View the selected location
The next cell will display the selected area on an interactive map.
Feel free to zoom in and out to get a better understanding of the area you'll be analysing.
Clicking on any point of the map will reveal the latitude and longitude coordinates of that point.

In [8]:
display_map(x=lon_range, y=lat_range)

## Dask computing environment

In EASI, each notebook starts by defining a Dask cluster for the notebook to use.

> For more information regarding Dask, see [A2 - Dask](A2%20-%20Dask.ipynb).

The are two main methods for setting up your dask cluster: 
1. **Local dask cluster**
    - Provides a dask multiprocessing environment on your Jupyter node. Useful for processing data volumes that don't exceed the Jupyter node limits, which are currently set at `cores = 8, memory = 32 GB` (2x large)


1. **Dask Gateway**
    - Provides a scalable compute cluster in EASI for your use. You can (*should*) use the same cluster across each of your notebooks (a separate cluster per notebook would unnessarily use EASI resources).
    - For most notebooks and data analysis start with `2 to 4 workers` (adaptive). Dask gateway is limited to 20 workers per user.
    - It is normal for this step to take **3 to 5 minutes** if new computing nodes need to be generated

**This notebook will just use a local cluster**

In [9]:
# Uses the older (collection 0) S2 L2A

# from easi_tools.load_s2l2a import load_s2l2a_with_offset

# query = dict(
#     product = 's2_l2a',
#     x = lon_range,
#     y = lat_range,
#     time = time_range
# )
# output_crs = notebook_utils.mostcommon_crs(dc, query)
# load_params = dict(
#     output_crs = output_crs,
#     resolution = (-10, 10),
#     dask_chunks = {'x':2048, 'y':2048},
#     group_by = 'solar_day'
# )
# ds = load_s2l2a_with_offset(
#     dc,
#     query | load_params   # Combine the two dicts that contain our search and load parameters
# )
# display(data)
# notebook_utils.xarray_object_size(data)

In [10]:
# Uses the new Collection 1 L2A

query = dict(
    product = 'sentinel_2_c1_l2a',
    x = lon_range,
    y = lat_range,
    time = time_range
)
output_crs = notebook_utils.mostcommon_crs(dc, query)
load_params = dict(
    output_crs = output_crs,
    resolution = (-10, 10),
    dask_chunks = {'x':2048, 'y':2048},
    group_by = 'solar_day',
    skip_broken_datasets = True,
)
data = dc.load(**(query | load_params))
display(notebook_utils.xarray_object_size(data))

# Apply valid data mask
# valid_mask = masking.valid_data_mask(data)
# ds = data.where(valid_mask)
good_pixel_flags = ['vegetation', 'not vegetated', 'water'] # [flags_def[str(i)] for i in [4, 5, 6]]
good_pixel_mask = enum_to_bool(data.scl, good_pixel_flags)
ds = data.where(good_pixel_mask)  # Apply good pixel mask (to all measurement layers)

# Apply scale and offset
# Matt says: Something odd in our setup .. offset=0 in the STAC record but offset=-0.1 in the product def
measurement_info = dc.list_measurements().loc[query['product']]
for vv in ds.data_vars:
    scale = measurement_info.loc[vv,'scale_factor']
    offset = 0 # measurement_info.loc[vv,'add_offset']
    if not pd.isnull(scale) and not pd.isnull(offset):
        # print(f'{vv}: {scale}, {offset}')
        ds[vv] = ds[vv] * scale + offset
        
display(ds)

'Dataset size: 407.88 MB'

<xarray.Dataset>
Dimensions:      (time: 29, y: 561, x: 848)
Coordinates:
  * time         (time) datetime64[ns] 2022-12-10T04:51:42.497000 ... 2023-04...
  * y            (y) float64 2.703e+06 2.703e+06 ... 2.698e+06 2.698e+06
  * x            (x) float64 6.416e+05 6.416e+05 6.416e+05 ... 6.5e+05 6.5e+05
    spatial_ref  int32 32645
Data variables: (12/17)
    coastal      (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    blue         (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    green        (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    red          (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    rededge1     (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    rededge2     (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    ...           ...
    swir22       (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    cloud        (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    snow         (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    scl          (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    aot          (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    wvp          (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
Attributes:
    crs:           EPSG:32645
    grid_mapping:  spatial_ref

In [11]:
# Calculate NDVI and EVI
# Borrowed from calculate_indices(ds, index=veg_proxy, satellite_mission="s2")

ndvi_da = (ds.nir - ds.red) / (ds.nir + ds.red)
evi_da = 2.5 * ((ds.nir - ds.red) / (ds.nir + 6 * ds.red - 7.5 * ds.blue + 1))

veg = ndvi_da.to_dataset(name='ndvi')
veg['evi'] = evi_da

display(veg)

<xarray.Dataset>
Dimensions:      (time: 29, y: 561, x: 848)
Coordinates:
  * time         (time) datetime64[ns] 2022-12-10T04:51:42.497000 ... 2023-04...
  * y            (y) float64 2.703e+06 2.703e+06 ... 2.698e+06 2.698e+06
  * x            (x) float64 6.416e+05 6.416e+05 6.416e+05 ... 6.5e+05 6.5e+05
    spatial_ref  int32 32645
Data variables:
    ndvi         (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>
    evi          (time, y, x) float32 dask.array<chunksize=(1, 561, 848), meta=np.ndarray>

# TODO

1. ~Calculate `ndvi` and `evi` into one xarray.Dataset~
1. ~Optional for viewing the data: Make a linked plot of NDVi and EVI (one column rather than side by side)~
   - ~Overlay the set of points~
1. Drill the set pf point and construct a pandas Dataframe with y (index) = dates and columns = points
   - Dataframe for each NDVI and EVI or together?
1. Make some cool plots of the NDVI and EVI time series
1. ....

In [12]:
%%time
veg.compute();

CPU times: user 206 ms, sys: 93.3 ms, total: 299 ms
Wall time: 19 s


In [13]:
import hvplot
p1 = veg.ndvi.hvplot.image(cmap='YlGn', title='NDVI') * gdf.to_crs(data.crs).hvplot(color='red')
p2 = veg.evi.hvplot.image(cmap='YlGn', title='EVI') * gdf.to_crs(data.crs).hvplot(color='red')
(p1 + p2).cols(1)

:Layout
   .DynamicMap.I  :DynamicMap   [time]
      :Overlay
         .Image.I  :Image   [x,y]   (ndvi)
         .Points.I :Points   [x,y]
   .DynamicMap.II :DynamicMap   [time]
      :Overlay
         .Image.I  :Image   [x,y]   (evi)
         .Points.I :Points   [x,y]

In [14]:

for i,p in enumerate(gdf['geometry']):
    print(f'{i}: {p.x}, {p.y}')
    xx = veg.sel(x=p.x, y=p.y, method='nearest')
    
    # we have dataframe for each point
    # todo:
    # - 
    
    break
print(xx.to_dataframe())

0: 88.4131613, 24.4253374
                                 y         x  spatial_ref      ndvi       evi
time                                                                         
2022-12-10 04:51:42.497  2697705.0  641565.0        32645 -0.176829 -0.083051
2022-12-15 04:51:45.616  2697705.0  641565.0        32645 -0.173984 -0.161469
2022-12-20 04:51:44.838  2697705.0  641565.0        32645 -0.157180 -0.168439
2022-12-25 04:51:44.005  2697705.0  641565.0        32645       NaN       NaN
2022-12-30 04:51:44.903  2697705.0  641565.0        32645       NaN       NaN
2023-01-04 04:51:44.920  2697705.0  641565.0        32645       NaN       NaN
2023-01-09 04:51:42.616  2697705.0  641565.0        32645 -0.189586 -0.158997
2023-01-14 04:51:43.075  2697705.0  641565.0        32645       NaN       NaN
2023-01-19 04:51:43.342  2697705.0  641565.0        32645 -0.104972 -0.113463
2023-01-24 04:51:42.431  2697705.0  641565.0        32645 -0.066667 -0.087220
2023-01-29 04:51:43.449  2697705.0  64